In [1]:
import numpy as np
import pandas as pd

from datetime import datetime, date, time, timedelta

import cufflinks
cufflinks.go_offline(connected=True)

from plotly.offline import init_notebook_mode, iplot
import plotly.express as px
init_notebook_mode(connected=True)

In [2]:
df = pd.read_pickle("./optimized.pkl")
df

Дата вылета Номер рейса Аэропорт вылета Аэропорт прилета  \
0     2024-08-01 00:00:00        1009             KGD              SVO   
1     2024-08-01 00:00:00        1018             SVO              KGD   
2     2024-08-01 00:00:00        1054             SVO              MCX   
3     2024-08-01 00:00:00        1055             MCX              SVO   
4     2024-08-01 00:00:00        1129             AER              SVO   
...                   ...         ...             ...              ...   
17217 2025-06-02 00:00:00         521             DXB              SVO   
17218 2025-06-02 00:00:00         526             SVO              DXB   
17219 2025-06-02 00:00:00        6321             LED              KGD   
17220 2025-06-02 00:00:00        6574             KJA              LED   
17221 2025-06-02 02:10:00        6792             SVX              KJA   

       Время вылета  Время прилета Тип ВС         Доход  Емкость  Пассажиры  \
0               180            395    32B   8377.470000      183        184   
1               735            830    32B  10233.260000      183        188   
2              1305             45    32A   8449.190000      150        147   
3               380            550    32A   8380.720000      150        158   
4              1210           1410    32A   8818.430000      158        102   
...             ...            ...    ...           ...      ...        ...   
17217           965           1265    73H  19393.452433      158         82   
17218           685           1100    73H  16626.772645      158         75   
17219           715            775    SU9   6452.582350      100         88   
17220           355            420    32A  20663.396703      158        157   
17221           130           1075    SU9  10610.556582      100         93   

       ...  Код страны аэропорта прилета  Расстояние между аэропортами  \
0      ...                            RU                   1069.140281   
1      ...                            RU                   1069.140281   
2      ...                            RU                   1636.244718   
3      ...                            RU                   1636.244718   
4      ...                            RU                   1403.718580   
...    ...                           ...                           ...   
17217  ...                            RU                   3708.223224   
17218  ...                            AE                   3708.223224   
17219  ...                            RU                    797.306136   
17220  ...                            RU                   3564.618155   
17221  ...                            RU                   1936.039938   

       Международный рейс  Вектор движения  Популяция аэропорта вылета  \
0                   False        76.692545                      475056   
1                   False       -89.422018                    10381222   
2                   False       149.034839                    10381222   
3                   False       -23.134074                      596356   
4                   False        -6.539875                      327608   
...                   ...              ...                         ...   
17217                True       -18.347831                     3478300   
17218                True       149.482012                    10381222   
17219               False      -129.051777                     5351935   
17220               False       -57.261267                     1090811   
17221               False        78.494856                     1495066   

       Часовой пояс аэропорта вылета  Популяция аэропорта прилета  \
0                 Europe/Kaliningrad                     10381222   
1                      Europe/Moscow                       475056   
2                      Europe/Moscow                       596356   
3                      Europe/Moscow                     10381222   
4                      Europe/Moscow                 

In [3]:
fig = px.scatter(
    df,
    x='Дата вылета',
    y='Доход',
    color='Номер рейса',
    symbol='stage',
    hover_data=['Аэропорт вылета', "Аэропорт прилета", "Страна аэропорта вылета", "Страна аэропорта прилета", "Время вылета", "Время прилета", "Расстояние между аэропортами"],
    trendline='ols'
)
fig.show()

In [4]:
df['Доход'] = df['Доход'].astype(int)

# суммарный прогноз по рейсам на каждом этапе
revenue_by_flight: pd.DataFrame = df.groupby(['Номер рейса', 'stage'])['Доход'].sum().unstack(fill_value=0)

# разница дохода
revenue_by_flight['delta'] = revenue_by_flight['result'] - revenue_by_flight['start']
revenue_by_flight['pct_change'] = (revenue_by_flight['result'] - revenue_by_flight['start']) / revenue_by_flight['start'] * 100

# сортируем по приросту
revenue_by_flight = revenue_by_flight.sort_values('delta', ascending=False)

revenue_by_flight

stage          result     start   delta  pct_change
Номер рейса                                        
427           4986337   4823438  162899    3.377238
1277          2736935   2586586  150349    5.812643
521          17108776  17008872   99904    0.587364
1246          2618272   2522127   96145    3.812060
526          11384857  11289672   95185    0.843116
6574          4237560   4144177   93383    2.253355
1055          2608493   2522506   85987    3.408793
6792          1416324   1333717   82607    6.193743
2143          7919408   7842488   76920    0.980811
1129          3495098   3426679   68419    1.996656
1018          2805730   2739920   65810    2.401895
1190          2198712   2137780   60932    2.850247
1525          6708031   6657050   50981    0.765820
225           9467386   9416893   50493    0.536196
2142          6532040   6490885   41155    0.634043
275          19364975  19326953   38022    0.196730
209          26261704  26223788   37916    0.144586
638           4692463   4660471   31992    0.686454
1054          2083013   2053235   29778    1.450297
1524          6808561   6779651   28910    0.426423
1009          2421423   2393333   28090    1.173677
1478          4277048   4252331   24717    0.581258
1141          3833760   3810107   23653    0.620796
851           1161589   1153855    7734    0.670275
6568          2556055   2548661    7394    0.290113
1713          9960203   9958172    2031    0.020395
6321           505224    503886    1338    0.265536
1276          2298029   2300226   -2197   -0.095512
1191          2206901   2216437   -9536   -0.430240
233          17430981  17442407  -11426   -0.065507
1479          4810438   4835086  -24648   -0.509774
224           8222326   8253754  -31428   -0.380772
321          29756606  29911873 -155267   -0.519082

In [5]:
# Строим график разницы дохода
fig = px.bar(
    revenue_by_flight.reset_index(),
    x='Номер рейса',
    y='delta',
    text=revenue_by_flight['pct_change'].apply(lambda x: f"{x:+.1f}%"),
    title='Прирост прогнозируемого дохода после оптимизации по рейсам',
    labels={'delta': 'Разница дохода (result - start)'}
)

fig.show()

In [6]:
revenue_by_flight.to_json("./damir.json", orient="records")

In [13]:
df.to_json("./massive.json", orient="records")
cdf = df.copy()

In [9]:
def combine_date_minutes(date_val, minutes):
    if pd.isna(date_val):
        return pd.NaT
    dt_date = pd.to_datetime(date_val).normalize()
    return dt_date + pd.to_timedelta(int(minutes), unit='m')

df['Время вылета_ts'] = df.apply(lambda r: combine_date_minutes(r['Дата вылета'], r['Время вылета']), axis=1)

In [14]:
df['Время вылета_ts'] = pd.to_datetime(df['Время вылета_ts'])
df = df[df['Время вылета_ts'] < '2024-08-03']

intervals = [15]

agg_list = []

for interval in intervals:
    slot_col = f'slot_{interval}m'
    df[slot_col] = df['Время вылета_ts'].dt.floor(f'{interval}T')
    
    counts = df.groupby(slot_col).size().reset_index(name='Количество вылетов')
    counts['Интервал'] = f'{interval} минут'
    counts.rename(columns={slot_col: 'Время слота'}, inplace=True)
    
    # чтобы x-ось была удобочитаемой, добавим строковое представление времени
    counts['Время слота str'] = counts['Время слота'].dt.strftime('%Y-%m-%d %H:%M')
    agg_list.append(counts)

df_counts = pd.concat(agg_list, ignore_index=True)

fig = px.bar(
    df_counts,
    x='Время слота str',
    y='Количество вылетов',
    color='Интервал',
    barmode='group',
    title='Количество вылетов по временным слотам'
)

fig.update_layout(
    xaxis_title='Время',
    yaxis_title='Количество вылетов',
    xaxis_tickangle=-45
)
fig.show()


/var/folders/xw/psrqspw174nc8yg0w2y8lxdh0000gn/T/ipykernel_5463/1674245680.py:10: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.



In [15]:
df = pd.read_pickle("./furryfemboy2007.pkl")
df

Дата вылета Номер рейса Аэропорт вылета Аэропорт прилета Время вылета  \
0      2024-08-01        1479             ABA              SVO     10:00:00   
1      2024-08-01         427             SSH              SVO     16:30:00   
2      2024-08-01         275             HKT              SVO     10:35:00   
3      2024-08-01         275             HKT              SVO     10:35:00   
4      2024-08-01         275             HKT              SVO     10:35:00   
...           ...         ...             ...              ...          ...   
38533  2025-06-02        1009             KGD              SVO     03:00:00   
38534  2025-06-02        1009             KGD              SVO     03:00:00   
38535  2025-06-02        1018             SVO              KGD     11:50:00   
38536  2025-06-02        1018             SVO              KGD     11:50:00   
38537  2025-06-02        1525             RGK              SVO     10:00:00   

      Время прилета  Емкость кабины  LF Кабина  Бронирования по кабинам  \
0          11:00:00             167     1.0299                      172   
1          22:30:00              28     0.1071                        3   
2          16:40:00             375     0.5467                      205   
3          16:40:00              24     0.2500                        6   
4          16:40:00              28     0.2500                        7   
...             ...             ...        ...                      ...   
38533      06:30:00              29     0.5517                       16   
38534      06:30:00             138     1.1014                      152   
38535      13:35:00              16     0.8750                       14   
38536      13:35:00             138     1.0290                      142   
38537      10:40:00             138     0.9130                      126   

      Тип ВС  ... Median Бронирования по кабинам  IQR Бронирования по кабинам  \
0        32B  ...                          176.0                          8.0   
1        333  ...                            9.0                          3.0   
2        77W  ...                          202.0                        117.0   
3        77W  ...                           12.0                         10.0   
4        77W  ...                           12.0                         11.0   
...      ...  ...                            ...                          ...   
38533    32B  ...                           22.0                         15.5   
38534    32B  ...                          152.0                         12.0   
38535    32B  ...                           11.0                          5.0   
38536    32B  ...                          145.0                         12.0   
38537    73H  ...                          135.0                         14.0   

       Min Пассажиры  Max Пассажиры  Median Пассажиры  IQR Пассажиры  \
0             151.74         184.26             176.0           8.00   
1               3.32          15.68               9.0           4.00   
2              69.56         290.44             213.0         109.00   
3               1.00          21.94              12.5          10.00   
4               2.04          26.92              12.0          11.00   
...              ...            ...               ...            ...   
38533           1.00          30.20              22.0          16.00   
38534         136.82         171.00             153.0          13.00   
38535           5.00          16.00              11.0           5.00   
38536         131.00         162.54             145.0          12.00   
38537         100.92         155.02             137.0          13.75   

          Время вылета_ts                     flight_id  was_moved   stage  
0     2024-08-01 10:00:00  1479_ABA_2024-08-01_10:00:00      False   start  
1     2024-08-01 16:30:00   427_SSH_2024-08-01_16:30:00      False   start  
2     2024-08-01 10:35:00   275_HKT_2024-08-01_10:35:00      False   start  
3     2024

In [ ]:
df_compare = pd.DataFrame({
    "Доход_до": df[df['stage'] == 'start'].groupby("Номер рейса")["Доход пасс"].sum(),
    "Доход_после": df[df['stage'] == 'result'].groupby("Номер рейса")["Доход пасс"].sum()
}).reset_index()

fig = px.scatter(df_compare, x="Доход_до", y="Доход_после", text="Номер рейса",
                 title="Доход рейсов: до vs после оптимизации")
fig.add_shape(type="line", x0=0, y0=0, x1=df_compare["Доход_до"].max(), 
              y1=df_compare["Доход_до"].max(), line=dict(color="red", dash="dash"))
fig.show()
